In [1]:
!python3 -V
import pDESy
pDESy.__version__

from IPython.display import Markdown
from pDESy.model.base_project import BaseProject
from pDESy.model.base_product import BaseProduct
from pDESy.model.base_component import BaseComponent
from pDESy.model.base_workflow import BaseWorkflow
from pDESy.model.base_task import BaseTask
from pDESy.model.base_task import BaseTaskDependency
from pDESy.model.base_team import BaseTeam
from pDESy.model.base_worker import BaseWorker
from pDESy.model.base_facility import BaseFacility
from pDESy.model.base_workplace import BaseWorkplace
from pDESy.model.base_priority_rule import TaskPriorityRuleMode,ResourcePriorityRuleMode

Python 3.13.5


製品定義

In [2]:
project = BaseProject("sample_workflow")

product = project.create_product("product")

A = product.create_component("A")
B = product.create_component("B")

ワークフロー定義・同一ワークフロー間依存関係

In [3]:
workflowA = project.create_workflow("workflowA")

task_A1 = workflowA.create_task("A1", default_work_amount=1.0)
task_A2 = workflowA.create_task("A2", default_work_amount=1.0)
task_A3 = workflowA.create_task("A3", default_work_amount=1.0)

A.update_targeted_task_set({task_A1, task_A2, task_A3})

task_A2.add_input_task(task_A1)
task_A3.add_input_task(task_A2)

In [4]:
workflowB = project.create_workflow("workflowB")

task_B1 = workflowB.create_task("B1", default_work_amount=1.0)
task_B2 = workflowB.create_task("B2", default_work_amount=1.0)
task_B3 = workflowB.create_task("B3", default_work_amount=1.0)

B.update_targeted_task_set({task_B1, task_B2, task_B3})

task_B2.add_input_task(task_B1)
task_B3.add_input_task(task_B2)

異なるワークフロー間依存関係

In [5]:
task_B1.add_input_task(task_A2)

設備・人員

In [6]:
# wrokplace model
placeA = project.create_workplace("placeA", max_space_size=10.0)
placeB = project.create_workplace("placeB", max_space_size=10.0)

facilityA = placeA.create_facility("facilityA", cost_per_time=1)
facilityB = placeB.create_facility("facilityB", cost_per_time=1)
facilityA.workamount_skill_mean_map = {task_A1.name:1.0,task_A2.name:1.0, task_A3.name:1.0} 
facilityB.workamount_skill_mean_map = {task_B1.name:1.0,task_B2.name:1.0, task_B3.name:1.0} 

#team model
team = project.create_team("team1")

wA = team.create_worker("workerA", cost_per_time=10.0)
wB = team.create_worker("workerB", cost_per_time=10.0)

wA.workamount_skill_mean_map = {task_A1.name:1.0,task_A2.name:1.0, task_A3.name:1.0} 
wB.workamount_skill_mean_map = {task_B1.name:1.0,task_B2.name:1.0, task_B3.name:1.0}

wA.facility_skill_map = {facilityA.name:1.0}
wB.facility_skill_map = {facilityB.name:1.0}

team.update_targeted_task_set({task_A1,task_A2,task_A3, task_B1,task_B2,task_B3})

placeA.update_targeted_task_set({task_A1,task_A2,task_A3})
placeB.update_targeted_task_set({task_B1,task_B2,task_B3})

In [7]:
project.simulate(max_time=200, progress_bar=True)

ValueError: Graph has a cycle. Topological sort failed.